In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

In [3]:
!pip install plotly

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 15.3/15.3 MB 74.5 MB/s eta 0:00:0000:0100:01


In [4]:
# from fastcore.basics import *
# from fastcore.parallel import *
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import roc_auc_score, roc_curve, precision_score, recall_score, f1_score, accuracy_score
from os import cpu_count
from math import floor
import pandas as pd
import numpy as np
from sklearn.linear_model import LinearRegression, LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import SVC
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
# from xgboost import XGBClassifier
# from lightgbm import LGBMClassifier
# from catboost import CatBoostClassifier
from sklearn.naive_bayes import GaussianNB
# import shap
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)
# shap.initjs()

In [5]:
data=pd.read_parquet("/project_ghent/raman/netflow_datasets/nftoniotv2/NF-ToN-IoT-V2.parquet")

## very very Basic EDA

In [6]:
data.dtypes

L4_SRC_PORT                      int32
L4_DST_PORT                      int32
PROTOCOL                          int8
L7_PROTO                       float32
IN_BYTES                         int32
IN_PKTS                          int32
OUT_BYTES                        int32
OUT_PKTS                         int32
TCP_FLAGS                        int16
CLIENT_TCP_FLAGS                 int16
SERVER_TCP_FLAGS                 int16
FLOW_DURATION_MILLISECONDS       int32
DURATION_IN                      int32
DURATION_OUT                     int32
MIN_TTL                          int16
MAX_TTL                          int16
LONGEST_FLOW_PKT                 int32
SHORTEST_FLOW_PKT                int16
MIN_IP_PKT_LEN                   int16
MAX_IP_PKT_LEN                   int32
SRC_TO_DST_SECOND_BYTES        float64
DST_TO_SRC_SECOND_BYTES        float64
RETRANSMITTED_IN_BYTES           int32
RETRANSMITTED_IN_PKTS            int16
RETRANSMITTED_OUT_BYTES          int32
RETRANSMITTED_OUT_PKTS   

In [7]:
data.Label.value_counts()

Label
1    9534597
0    3601284
Name: count, dtype: int64

In [8]:
data.Attack.value_counts()

Attack
Benign        3601284
scanning      3002169
xss           2449955
ddos          1746590
password       993718
injection      660467
dos            654359
backdoor        16259
mitm             7723
ransomware       3357
Name: count, dtype: int64

In [9]:
data=data.drop(columns=['L4_SRC_PORT', 'L4_DST_PORT']) #dropping metadata

## Finding contaminant features using XAI (SHAP)
goal: 
- try to find the contaminant features that have blanked predictive power across all attack classes

method:
* look for shap values per feature that are consistantly high or low among all attack classes.
   
how:
```
possible_contaminants =[]
    while models can achive high accuracy{
    
        * Train a binary classification model (e.g., xgboost) on different attack classes and benign class
        * For each model, calculate shappley values on test set
        * For each model, use np.abs(shap_values).mean(0) to compute the mean absolute SHAP value for each feature across all samples. 
          This will give you a measure of how much each feature contributes to the model output on average across all samples (the importance).
          
        * normalize importances across for each attack class sum of feature importances equals 1
        * for each feature, calculate variance of importance for each attack class
        * for each feature, calculate average importance across all attack classes
        * score of a feature is the weighted sum of the importance and variance
        
        * feature F is feature with the highest score
        * possible_contaminants.append(F)
        * drop F from dataset
    }
```

In [10]:
training_set = data.sample(frac=0.3, replace=False,random_state=42)
# 1%train, 99% test
testing_set = data.drop(index=training_set.index)

In [11]:
training_set.Attack.value_counts()

Attack
Benign        1080399
scanning       901211
xss            734104
ddos           523655
password       297668
injection      198421
dos            197104
backdoor         4842
mitm             2360
ransomware       1000
Name: count, dtype: int64

In [12]:
attacks=training_set.Attack.unique()
attacks=[ 'Benign','ddos', 'dos', 'scanning', 'xss', 'injection',
       'password', 'mitm', 'backdoor', 'ransomware']
attacks

['Benign',
 'ddos',
 'dos',
 'scanning',
 'xss',
 'injection',
 'password',
 'mitm',
 'backdoor',
 'ransomware']

### Correlated features

In [13]:
# corr = training_set.corr()
# corr_features={corr.columns[i] : corr.columns[(corr>0.9).iloc[i]].values.tolist() for i in range(0,corr.shape[0])}
# corr_list=[]
# for key,value in corr_features.items():
# #     check if we already have this set
#     have_set=False
#     for set_s in corr_list:
#         if key in set_s:
# #             we have found a set
#             have_set=True
#             break
#     if have_set==False and len(value)>1:
#         corr_list.append(value)

In [14]:
# corr_list

In [15]:
# #dropping all but one feature per correlation group
# for i in range(len(corr_list)):
#     training_set.drop(columns=corr_list[i][1:],inplace=True)
#     testing_set.drop(columns=corr_list[i][1:],inplace=True)

### split into dataframes per attack class

In [16]:
grouped = training_set.groupby(training_set.Attack)
dfs={cat:grouped.get_group(cat) for cat in attacks[1:]}
dfs[attacks[0]]=grouped.get_group(attacks[0]) #don't subsample normal attacks
#dfs key=attack_cat, value is dataframe 

In [17]:
# to make calculations faster
for k,v in dfs.items():
    if v.shape[0]>10000:
        dfs[k]=v.sample(10000,replace=False)

In [18]:
for atk_type in attacks[1:]:
    normals_to_sample = dfs[atk_type].shape[0]
#     print(normals_to_sample)
    normals_sample = dfs['Benign'].sample(normals_to_sample)
#     dfs['Normal'] = dfs['Normal'].drop(index=normals_sample.index)#don't resample
    dfs[atk_type] = pd.concat(objs=[dfs[atk_type], normals_sample])
    print(dfs[atk_type].shape[0], normals_sample.shape[0], dfs['Benign'].shape[0])

20000 10000 10000
20000 10000 10000
20000 10000 10000
20000 10000 10000
20000 10000 10000
20000 10000 10000
4720 2360 10000
9684 4842 10000
2000 1000 10000


In [19]:
testing_dfs = {}
grouped = testing_set.groupby(testing_set.Attack)
testing_dfs={cat:grouped.get_group(cat) for cat in attacks[1:]}
testing_dfs[attacks[0]]=grouped.get_group(attacks[0]) #don't subsample normal attacks
#testing_dfs key=attack_cat, value is dataframe 

In [20]:
#to make calculations faster
for k,v in testing_dfs.items():
    if v.shape[0]>10000:
        testing_dfs[k]=v.sample(10000,replace=False)

In [21]:
for atk_type in attacks[1:]:
    normals_to_sample = testing_dfs[atk_type].shape[0] 
    normals_sample = testing_dfs['Benign'].sample(normals_to_sample)
#     testing_dfs['Normal'] = testing_dfs['Normal'].drop(index=normals_sample.index)#don't resample
    testing_dfs[atk_type] = pd.concat(objs=[testing_dfs[atk_type], normals_sample])
    print(testing_dfs[atk_type].shape[0], normals_sample.shape[0], testing_dfs['Benign'].shape[0])

20000 10000 10000
20000 10000 10000
20000 10000 10000
20000 10000 10000
20000 10000 10000
20000 10000 10000
10726 5363 10000
20000 10000 10000
4714 2357 10000


In [22]:
print(f"TRAINING SETS")
for k,v in dfs.items():
    v.drop(columns=['Attack'], inplace=True)   
    print(k, v.shape)
    print(v['Label'].value_counts())

TRAINING SETS
ddos (20000, 40)
Label
1    10000
0    10000
Name: count, dtype: int64
dos (20000, 40)
Label
1    10000
0    10000
Name: count, dtype: int64
scanning (20000, 40)
Label
1    10000
0    10000
Name: count, dtype: int64
xss (20000, 40)
Label
1    10000
0    10000
Name: count, dtype: int64
injection (20000, 40)
Label
1    10000
0    10000
Name: count, dtype: int64
password (20000, 40)
Label
1    10000
0    10000
Name: count, dtype: int64
mitm (4720, 40)
Label
1    2360
0    2360
Name: count, dtype: int64
backdoor (9684, 40)
Label
1    4842
0    4842
Name: count, dtype: int64
ransomware (2000, 40)
Label
1    1000
0    1000
Name: count, dtype: int64
Benign (10000, 40)
Label
0    10000
Name: count, dtype: int64


In [23]:
print("TESTING SETS")
for k,v in testing_dfs.items():
    v.drop(columns=['Attack'], inplace=True)   
    print(k, v.shape)
    print(v['Label'].value_counts())

TESTING SETS
ddos (20000, 40)
Label
1    10000
0    10000
Name: count, dtype: int64
dos (20000, 40)
Label
1    10000
0    10000
Name: count, dtype: int64
scanning (20000, 40)
Label
1    10000
0    10000
Name: count, dtype: int64
xss (20000, 40)
Label
1    10000
0    10000
Name: count, dtype: int64
injection (20000, 40)
Label
1    10000
0    10000
Name: count, dtype: int64
password (20000, 40)
Label
1    10000
0    10000
Name: count, dtype: int64
mitm (10726, 40)
Label
1    5363
0    5363
Name: count, dtype: int64
backdoor (20000, 40)
Label
1    10000
0    10000
Name: count, dtype: int64
ransomware (4714, 40)
Label
1    2357
0    2357
Name: count, dtype: int64
Benign (10000, 40)
Label
0    10000
Name: count, dtype: int64


In [24]:
training_dfs=dfs

In [25]:
import plotly.express as px

### TCP_WIN_MAX_IN

In [26]:
attacks

['Benign',
 'ddos',
 'dos',
 'scanning',
 'xss',
 'injection',
 'password',
 'mitm',
 'backdoor',
 'ransomware']

In [30]:
%matplotlib inline


In [33]:
!jupyter labextension list

JupyterLab v3.6.3
/opt/conda/share/jupyter/labextensions
        jupyterlab_pygments v0.2.2 enabled OK (python, jupyterlab_pygments)
        jupyterlab-plotly v5.14.1 enabled OK
        jupyter-matplotlib v0.11.3 enabled OK
        nbdime-jupyterlab v2.2.0 enabled OK
        @jupyter-widgets/jupyterlab-manager v5.0.7 enabled OK (python, jupyterlab_widgets)
        @jupyterlab/git v0.41.0 enabled OK (python, jupyterlab-git)

Other labextensions (built into JupyterLab)
   app dir: /opt/conda/share/jupyter/lab



In [31]:
for attack in attacks[1:]:
    fig=px.histogram(
    training_dfs[attack],
    x='TCP_WIN_MAX_IN',
    color='Label',
    marginal='box',
    barmode='group',
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

In [32]:
(training_set.groupby('Attack')['TCP_WIN_MAX_IN'].apply(lambda x: ((x==29200) | (x==4049)| (x==0)| (x==4096)| (x==8192)).mean())*100).reset_index(name='Percentage')

Attack  Percentage
0      Benign   21.203555
1    backdoor   99.690211
2        ddos   98.100467
3         dos   93.167566
4   injection   97.285066
5        mitm   99.025424
6    password   95.310883
7  ransomware   84.900000
8    scanning   91.133264
9         xss   99.227221

### LONGEST_FLOW_PKT

In [ ]:
import math
for attack in attacks[1:]:
    d=training_dfs[attack]#[training_dfs[attack].ICMP_TYPE<=1000000]
    k=d#[training_dfs[attack].Label==1]
#     k=k[k.DST_TO_SRC_AVG_THROUGHPUT>0]
    bin_width= 10000
    # here you can choose your rounding method, I've chosen math.ceil
    nbins = math.ceil((k["LONGEST_FLOW_PKT"].max() - k["LONGEST_FLOW_PKT"].min()) / bin_width)
    fig=px.histogram(
    k,
    x='LONGEST_FLOW_PKT',
    color='Label',
    marginal='box',
    barmode='group',#nbins=nbins,
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

In [ ]:
(training_set.groupby('Attack')['LONGEST_FLOW_PKT'].apply(lambda x: ((x<60)).mean())*100).reset_index(name='Percentage')

### SRC_TO_DST_AVG_THROUGHPUT

In [ ]:
import math
for attack in attacks[1:]:
    d=training_dfs[attack][training_dfs[attack].SRC_TO_DST_AVG_THROUGHPUT<=1000000]
    k=d#[training_dfs[attack].Label==1]
#     k=k[k.DST_TO_SRC_AVG_THROUGHPUT>0]
    bin_width= 10000
    # here you can choose your rounding method, I've chosen math.ceil
    nbins = math.ceil((k["SRC_TO_DST_AVG_THROUGHPUT"].max() - k["SRC_TO_DST_AVG_THROUGHPUT"].min()) / bin_width)
    fig=px.histogram(
    k,
    x='SRC_TO_DST_AVG_THROUGHPUT',
    color='Label',
    marginal='box',
    barmode='group',#nbins=nbins,
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

In [ ]:
(training_set.groupby('Attack')['SRC_TO_DST_AVG_THROUGHPUT'].apply(lambda x: ((x>520000)|(x<100000)|(x==384000)).mean())*100).reset_index(name='Percentage')

### IN_BYTES

In [ ]:
import math
for attack in attacks[1:]:
    d=training_dfs[attack]#[training_dfs[attack].IN_BYTES<=10000]
    k=d#[training_dfs[attack].Label==1]
#     k=k[k.DST_TO_SRC_AVG_THROUGHPUT>0]
    bin_width= 100
    # here you can choose your rounding method, I've chosen math.ceil
    nbins = math.ceil((k["IN_BYTES"].max() - k["IN_BYTES"].min()) / bin_width)
    fig=px.histogram(
    k,
    x='IN_BYTES',
    color='Label',
    marginal='box',
    barmode='group',#nbins=nbins,
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

In [ ]:
training_set.groupby('Attack')['IN_BYTES'].apply(lambda x: ((x>142)|(x.between(61,76)|(x==48))).mean() * 100)

### min_ttl

In [ ]:
px.histogram(training_set, x="MIN_TTL",color="Label",barmode='group',histnorm='percent')

In [ ]:
training_set.groupby(["Label","MIN_TTL"]).MIN_TTL.count()

In [ ]:
training_set.groupby('Attack')['MIN_TTL'].apply(lambda x : ((x==0)|(x==64)|(x==128)).mean()*100)

In [ ]:
training_dfs["backdoor"].MIN_TTL

In [ ]:
for attack in attacks[1:]:
    fig=px.histogram(
    training_dfs[attack],
    x='MIN_TTL',
    color='Label',
    marginal='box',
    barmode='group',
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

### MIN_IP_PKT_LEN

In [ ]:
for attack in attacks[1:]:
    fig=px.histogram(
    training_dfs[attack],
    x='MIN_IP_PKT_LEN',
    color='Label',    barmode='group',

    marginal='box',
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

In [ ]:
(training_set.groupby('Attack')['MIN_IP_PKT_LEN'].apply(lambda x: ((x>=50)).mean())*100).reset_index(name='Percentage')

### SHORTEST_FLOW_PKT

In [ ]:
for attack in attacks[1:]:
    fig=px.histogram(
    training_dfs[attack],
    x='SHORTEST_FLOW_PKT',
    color='Label',
    marginal='box',
    barmode='group',
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

In [ ]:
(training_set.groupby('Attack')['SHORTEST_FLOW_PKT'].apply(lambda x: ((x<52)).mean())*100).reset_index(name='Percentage')

### TCP_FLAGS

In [ ]:
for attack in attacks[1:]:
    fig=px.histogram(
    training_dfs[attack],
    x='TCP_FLAGS',
    color='Label',
    marginal='box',
    barmode='group',
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

In [ ]:
training_set.groupby('Attack')['TCP_FLAGS'].apply(lambda x: ((x ==0)|(x ==27)|(x ==31)|(x ==22)).mean() * 100)

### TCP_WIN_MAX_OUT

In [ ]:
for attack in attacks[1:]:
    fig=px.histogram(
    training_dfs[attack],
    x='TCP_WIN_MAX_OUT',
    color='Label',
    marginal='box',
    barmode='group',
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

In [ ]:
training_set.groupby('Attack')['TCP_WIN_MAX_OUT'].apply(lambda x: ((x ==0)).mean() * 100)

### TCP_WIN_MAX_IN

In [ ]:
for attack in attacks[1:]:
    fig=px.histogram(
    training_dfs[attack],
    x='TCP_WIN_MAX_IN',
    color='Label',
    marginal='box',
    barmode='group',
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

### DST_TO_SRC_SECOND_BYTES

In [ ]:
import math
for attack in attacks[1:]:
    d=training_dfs[attack][training_dfs[attack].DST_TO_SRC_SECOND_BYTES<=1000000]
    k=d#[d.Label==1]
    bin_width= 1000
    # here you can choose your rounding method, I've chosen math.ceil
    nbins = math.ceil((k["DST_TO_SRC_SECOND_BYTES"].max() - k["DST_TO_SRC_SECOND_BYTES"].min()) / bin_width)
    fig=px.histogram(
    k,
    x='DST_TO_SRC_SECOND_BYTES',
    color='Label',#nbins=nbins,
    marginal='box',
    barmode='group',
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

In [ ]:
(training_set.groupby('Attack')['DST_TO_SRC_SECOND_BYTES'].apply(lambda x: ((x>64)).mean())*100).reset_index(name='Percentage')

### OUT_BYTES

In [ ]:
import math
for attack in attacks[1:]:
    d=training_dfs[attack][training_dfs[attack].DST_TO_SRC_SECOND_BYTES<=1000000]
    k=d#[d.Label==1]
    bin_width= 100
    # here you can choose your rounding method, I've chosen math.ceil
    nbins = math.ceil((k["OUT_BYTES"].max() - k["OUT_BYTES"].min()) / bin_width)
    fig=px.histogram(
    k,
    x='OUT_BYTES',
    color='Label',
    marginal='box',
    barmode='group',#nbins=nbins,
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

In [ ]:
training_set.groupby('Attack')['OUT_BYTES'].apply(lambda x: (x >50).mean() * 100)

### DST_TO_SRC_AVG_THROUGHPUT

In [ ]:
import math
for attack in attacks[1:]:
#     d=training_dfs[attack][training_dfs[attack].DST_TO_SRC_SECOND_BYTES<=1000000]
    k=training_dfs[attack]#[training_dfs[attack].Label==1]
    k=k[k.DST_TO_SRC_AVG_THROUGHPUT>0]
    bin_width= 100000
    # here you can choose your rounding method, I've chosen math.ceil
    nbins = math.ceil((k["DST_TO_SRC_AVG_THROUGHPUT"].max() - k["DST_TO_SRC_AVG_THROUGHPUT"].min()) / bin_width)
    fig=px.histogram(
    k,
    x='DST_TO_SRC_AVG_THROUGHPUT',
    color='Label',
    marginal='box',
    barmode='group',#nbins=nbins,
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

In [ ]:
(training_set.groupby('Attack')['DST_TO_SRC_AVG_THROUGHPUT'].apply(lambda x: ((x>417000)).mean())*100).reset_index(name='Percentage')

### NUM_PKTS_UP_TO_128_BYTES

In [ ]:
import math
for attack in attacks[1:]:
#     d=training_dfs[attack][training_dfs[attack].DST_TO_SRC_SECOND_BYTES<=1000000]
    k=training_dfs[attack][training_dfs[attack].Label==1]
    k=k[k.NUM_PKTS_UP_TO_128_BYTES>0]
    bin_width= 5
#     here you can choose your rounding method, I've chosen math.ceil
    nbins = math.ceil((k["NUM_PKTS_UP_TO_128_BYTES"].max() - k["NUM_PKTS_UP_TO_128_BYTES"].min()) / bin_width)
    fig=px.histogram(
    k,
    x='NUM_PKTS_UP_TO_128_BYTES',
    color='Label',
    marginal='box',
    barmode='group',nbins=nbins,
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

In [ ]:
training_set.groupby('Attack')['NUM_PKTS_UP_TO_128_BYTES'].apply(lambda x: ((x<=2)).mean() * 100)

### IN_PKTS

In [ ]:
import math
for attack in attacks[1:]:
#     d=training_dfs[attack][training_dfs[attack].DST_TO_SRC_SECOND_BYTES<=1000000]
    k=training_dfs[attack][training_dfs[attack].Label==1]
#     k=k[k.DST_TO_SRC_AVG_THROUGHPUT>0]
    bin_width= 5
    # here you can choose your rounding method, I've chosen math.ceil
    nbins = math.ceil((k["IN_PKTS"].max() - k["IN_PKTS"].min()) / bin_width)
    fig=px.histogram(
    k,
    x='IN_PKTS',
    color='Label',
    marginal='box',
    barmode='group',nbins=nbins,
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

In [ ]:
training_set.groupby('Attack')['IN_PKTS'].apply(lambda x: ((x==1)).mean() * 100)

### SRC_TO_DST_SECOND_BYTES

In [ ]:
import math
for attack in attacks[1:]:
    d=training_dfs[attack]#[training_dfs[attack].SRC_TO_DST_SECOND_BYTES<=1000000]
    k=d#[training_dfs[attack].Label==1]
    k=k[k.SRC_TO_DST_SECOND_BYTES<=1000000]
    bin_width= 100
    # here you can choose your rounding method, I've chosen math.ceil
    nbins = math.ceil((k["SRC_TO_DST_SECOND_BYTES"].max() - k["SRC_TO_DST_SECOND_BYTES"].min()) / bin_width)
    fig=px.histogram(
    k,
    x='SRC_TO_DST_SECOND_BYTES',
    color='Label',
    marginal='box',
    barmode='group',#nbins=nbins,
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

In [ ]:
training_set.groupby('Attack')['SRC_TO_DST_SECOND_BYTES'].apply(lambda x: ((x>150)|(x==48)|(x==67)|(x.between(61,71))).mean() * 100)

### ICMP_TYPE

In [ ]:
import math
for attack in attacks[1:]:
    d=training_dfs[attack]#[training_dfs[attack].ICMP_TYPE<=1000000]
    k=d#[training_dfs[attack].Label==1]
    k=k[k.ICMP_TYPE>0]
    bin_width= 1000
    # here you can choose your rounding method, I've chosen math.ceil
    #nbins = math.ceil((k["ICMP_TYPE"].max() - k["ICMP_TYPE"].min()) / bin_width)
    fig=px.histogram(
    k,
    x='ICMP_TYPE',
    color='Label',
    marginal='box',
    barmode='group',#nbins=nbins,
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

In [ ]:
(training_set.groupby('Attack')['ICMP_TYPE'].apply(lambda x: ((x==0)|(x==0)).mean())*100).reset_index(name='Percentage')

In [ ]:
(training_set[training_set.ICMP_TYPE>0].groupby('Attack')['ICMP_TYPE'].apply(lambda x: ((x==35840)|(x==771)).mean())*100).reset_index(name='Percentage')

### L7_PROTO

In [ ]:
import math
for attack in attacks[1:]:
    d=training_dfs[attack]#[training_dfs[attack].ICMP_TYPE<=1000000]
    k=d[training_dfs[attack].Label==1]
#     k=k[k.DST_TO_SRC_AVG_THROUGHPUT>0]
    bin_width= 5
    # here you can choose your rounding method, I've chosen math.ceil
    nbins = math.ceil((k["L7_PROTO"].max() - k["L7_PROTO"].min()) / bin_width)
    fig=px.histogram(
    k,
    x='L7_PROTO',
    color='Label',
    marginal='box',
    barmode='group',nbins=nbins,
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

In [ ]:
(training_set.groupby('Attack')['L7_PROTO'].apply(lambda x: ((x==7)|(x==41)|(x==7)|(x==131)|(x==91)).mean())*100).reset_index(name='Percentage')

### PROTOCOL

In [ ]:
training_set.groupby('Attack')['PROTOCOL'].apply(lambda x: ((x==6)|(x==17)).mean() * 100)

### CLIENT_TCP_FLAGS

In [ ]:
for attack in attacks[1:]:
    fig=px.histogram(
    training_dfs[attack],
    x='CLIENT_TCP_FLAGS',
    color='Label',
    marginal='box',
    barmode='group',
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

In [ ]:
training_set.groupby('Attack')['CLIENT_TCP_FLAGS'].apply(lambda x: ((x !=2)& (x!=0)).mean() * 100)

### FLOW_DURATION_MILLISECONDS

In [ ]:
for attack in attacks[1:]:
    fig=px.histogram(
    training_dfs[attack],
    x='FLOW_DURATION_MILLISECONDS',
    color='Label',
    marginal='box',
    barmode='group',
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

### DURATION_OUT

In [ ]:
for attack in attacks[1:]:
    fig=px.histogram(
    training_dfs[attack][training_dfs[attack].Label>0],
    x='DURATION_OUT',
    color='Label',
    marginal='box',
    barmode='group',
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

In [ ]:
training_set.groupby('Attack')['DURATION_OUT'].apply(lambda x: (x ==0).mean() * 100).reset_index(name='Percentage')

### NUM_PKTS_128_TO_256_BYTES

In [ ]:
for attack in attacks[1:]:
    fig=px.histogram(
    training_dfs[attack],#[training_dfs[attack].Label>0],
    x='NUM_PKTS_128_TO_256_BYTES',
    color='Label',
    marginal='box',
    barmode='group',
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

In [ ]:
(training_set.groupby('Attack')['NUM_PKTS_128_TO_256_BYTES'].apply(lambda x: ((x==0)|(x<=2)).mean())*100).reset_index(name='Percentage')

### SERVER_TCP_FLAGS

In [ ]:
import math
for attack in attacks[1:]:
    d=training_dfs[attack]#[training_dfs[attack].SRC_TO_DST_SECOND_BYTES<=1000000]
    k=d#[training_dfs[attack].Label==1]
#     k=k[k.DST_TO_SRC_AVG_THROUGHPUT>0]
    bin_width= 100
    # here you can choose your rounding method, I've chosen math.ceil
    nbins = math.ceil((k["SERVER_TCP_FLAGS"].max() - k["SERVER_TCP_FLAGS"].min()) / bin_width)
    fig=px.histogram(
    k,
    x='SERVER_TCP_FLAGS',
    color='Label',
    marginal='box',
    barmode='group',#nbins=nbins,
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

In [ ]:
(training_set.groupby('Attack')['SERVER_TCP_FLAGS'].apply(lambda x: ((x==0)|(x==20)|(x==22)|(x==27)).mean())*100).reset_index(name='Percentage')

### NUM_PKTS_512_TO_1024_BYTES

In [ ]:
import math
for attack in attacks[1:]:
    d=training_dfs[attack]#[training_dfs[attack].NUM_PKTS_512_TO_1024_BYTES<=10000]
    k=d[training_dfs[attack].Label==1]
#     k=k[k.DST_TO_SRC_AVG_THROUGHPUT>0]
    bin_width= 5
    # here you can choose your rounding method, I've chosen math.ceil
    nbins = math.ceil((k["NUM_PKTS_512_TO_1024_BYTES"].max() - k["NUM_PKTS_512_TO_1024_BYTES"].min()) / bin_width)
    fig=px.histogram(
    k,
    x='NUM_PKTS_512_TO_1024_BYTES',
    color='Label',
    marginal='box',
    barmode='group',#nbins=nbins,
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

In [ ]:
(training_set.groupby('Attack')['NUM_PKTS_512_TO_1024_BYTES'].apply(lambda x: ((x<=1)).mean())*100).reset_index(name='Percentage')

### NUM_PKTS_256_TO_512_BYTES

In [ ]:
import math
for attack in attacks[1:]:
    d=training_dfs[attack]#[training_dfs[attack].NUM_PKTS_512_TO_1024_BYTES<=10000]
    k=d[training_dfs[attack].Label==1]
#     k=k[k.DST_TO_SRC_AVG_THROUGHPUT>0]
    bin_width= 5
    # here you can choose your rounding method, I've chosen math.ceil
    nbins = math.ceil((k["NUM_PKTS_256_TO_512_BYTES"].max() - k["NUM_PKTS_256_TO_512_BYTES"].min()) / bin_width)
    fig=px.histogram(
    k,
    x='NUM_PKTS_256_TO_512_BYTES',
    color='Label',
    marginal='box',
    barmode='group',#nbins=nbins,
    color_discrete_sequence=['turquoise','blue'],histnorm='percent',title=attack)
    fig.show()

In [ ]:
(training_set.groupby('Attack')['NUM_PKTS_256_TO_512_BYTES'].apply(lambda x: ((x<=1)).mean())*100).reset_index(name='Percentage')